<a href="https://www.databricks.com/solutions/accelerators"><img src='https://github.com/databricks-industry-solutions/.github/raw/main/profile/solacc_logo_wide.png'></img></a>

# GenAI slack bot companion notebook

*Sed ut perspiciatis unde omnis iste natus error sit voluptatem accusantium doloremque laudantium, totam rem aperiam,
eaque ipsa quae ab illo inventore veritatis et quasi architecto beatae vitae dicta sunt explicabo.
Nemo enim ipsam voluptatem quia voluptas sit aspernatur aut odit aut fugit, sed quia consequuntur magni dolores
eos qui ratione voluptatem sequi nesciunt. Neque porro quisquam est, qui dolorem ipsum quia dolor sit amet,
consectetur, adipisci velit, sed quia non numquam eius modi tempora incidunt ut labore et dolore magnam aliquam
quaerat voluptatem. Ut enim ad minima veniam, quis nostrum exercitationem ullam corporis suscipit laboriosam,
nisi ut aliquid ex ea commodi consequatur? Quis autem vel eum iure reprehenderit qui in ea voluptate velit esse
quam nihil molestiae consequatur, vel illum qui dolorem eum fugiat quo voluptas nulla pariatur?*

___

<antoine.amend@databricks.com>

___

In [0]:
%pip install "git+https://github.com/langchain-ai/langchain.git@master#subdirectory=libs/langchain" "git+https://github.com/mlflow/mlflow.git@gateway-migration" databricks-vectorsearch==0.21 databricks-sdk==0.12.0 mlflow[databricks] goose3==3.1.17 beautifulsoup4==4.10.0
dbutils.library.restartPython()

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
  Cloning https://github.com/langchain-ai/langchain.git (to revision master) to /tmp/pip-req-build-od1367o9
  Running command git clone --filter=blob:none --quiet https://github.com/langchain-ai/langchain.git /tmp/pip-req-build-od1367o9
  Resolved https://github.com/langchain-ai/langchain.git to commit db6bf8b022c17353b46f97ab3b9f44ff9e88a488
  Installing build dependencies: started
  Installing build dependencies: finished with status 'done'
  Getting requirements to build wheel: started
  Getting requirements to build wheel: finished with status 'done'
  Preparing metadata (pyproject.toml): started
  Preparing metadata (pyproject.toml): finished with status 'done'
  Cloning https://github.com/mlflow/mlflow.git (to revision gateway-migration) to /tmp/pip-req-build-ffz7tcx7
  Running command git clone --filter=blob:none --quiet https://github.com/mlflow/mlflow.git /tmp/pip-req-build-

Please modify below configuration variables such as unity catalog, database and schema names

In [0]:
uc_catalog_name = 'antoine_amend'
uc_schema_name = 'sgtm_genai'
uc_table_name = 'solution_accelerators'
uc_model_name = 'slack-bot-genai'

vs_endpoint_name = 'shared-demo-endpoint'
vs_index_name = 'solution_accelerators_vectors'

db_secret_scope = 'aamend'
db_secret_key = 'databricks_api_token'

Your Model Serving Endpoint will need a secret to authenticate against your Vector Search Index (see [Documentation](https://docs.databricks.com/en/security/secrets/secrets.html)).  <br/>
- You'll need to setup the Databricks CLI on your laptop or using this cluster terminal: <br/>
`pip install databricks-cli` <br/>
- Configure the CLI. You'll need your workspace URL and a PAT token from your profile page<br>
`databricks configure`
- Create the {db_secret_scope} scope:<br/>
`databricks secrets create-scope {db_secret_scope}`
- Save your service principal secret. It will be used by the Model Endpoint to autenticate. If this is a demo/test, you can use one of your PAT token.<br>
`databricks secrets put-secret {db_secret_scope} {db_secret_key}`

*Note: If using a service principal in lieu of personal token (recommended), make sure your service principal has access to the Vector Search index:*

```
# Grant USAGE access to catalog and schema
_ = spark.sql('GRANT USAGE ON CATALOG <catalog> TO `<YOUR_SP>`');
_ = spark.sql('GRANT USAGE ON DATABASE <catalog>.<db> TO `<YOUR_SP>`');

# Grant read access to vector index
from databricks.sdk import WorkspaceClient
import databricks.sdk.service.catalog as c
WorkspaceClient().grants.update(c.SecurableType.TABLE, <index_name>, changes=[c.PermissionsChange(add=[c.Privilege["SELECT"]], principal="<YOUR_SP>")])
  ```

In [0]:
try:
  dbutils.secrets.get(scope=db_secret_scope, key=db_secret_key)
except:
  raise Exception("This solution will need a secret to work")

In [0]:
# # Should you need to delete database
# from databricks.vector_search.client import VectorSearchClient
# vsc = VectorSearchClient(disable_notice=True)
# vs_index_fqn = f'{uc_catalog_name}.{uc_schema_name}.{vs_index_name}'
# vsc.delete_index(endpoint_name = vs_endpoint_name, index_name=vs_index_fqn)

# # Should you need to delete database schema
# spark.sql(f'DROP SCHEMA `{uc_catalog_name}`.`{uc_schema_name}` CASCADE')

[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True to VectorSearchClient().


DataFrame[]

In [0]:
_ = sql(f'CREATE CATALOG IF NOT EXISTS {uc_catalog_name}')
_ = sql(f'CREATE DATABASE IF NOT EXISTS {uc_catalog_name}.{uc_schema_name}')

# 1. Vector Store
In order to build that demo / MVP, we will extract key informations from our own solution accelerator program. 

In [0]:
uc_table_fqn = f'{uc_catalog_name}.{uc_schema_name}.{uc_table_name}'
vs_index_fqn = f'{uc_catalog_name}.{uc_schema_name}.{vs_index_name}'

## 1.1 download data
Scraping our github pages

In [0]:
from bs4 import BeautifulSoup
import requests
from io import BytesIO
from goose3 import Goose

def get_repos():
  solutions = []
  index_url = 'https://github.com/orgs/databricks-industry-solutions/repositories?page=1&type=Repositories'
  response = requests.get(index_url)
  soup = BeautifulSoup(response.text, features="html.parser")
  links = [link.get('href') for link in soup.findAll('a')]
  pages = get_pages(links)
  for page in pages:
    print(f'Scraping page {page}')
    index_url = f'https://github.com{page}'
    response = requests.get(index_url)
    soup = BeautifulSoup(response.text, features="html.parser")
    links = soup.findAll('a', {'data-hovercard-type': 'repository'})
    links = [link.get('href') for link in links]
    for link in links:
      solutions.append(f'https://github.com{link}')
  print(f'Found {len(solutions)} solution accelerator(s)')
  return solutions

def get_pages(links):
  pages = ['/orgs/databricks-industry-solutions/repositories?page=1&type=Repositories']
  for link in links:
    if '/orgs/databricks-industry-solutions/repositories?' in link:
      pages.append(link)
  return set(pages)

def get_name(url):
  return url.split('/')[-1]

def scrape_solution(url):
  goose = Goose()
  article = goose.extract(url=url)
  text = article.cleaned_text
  text = text \
    .replace('”', '"') \
    .replace('“', '"') \
    .replace('‘', '\'') \
    .replace('’', '\'')
  return text

In [0]:
import pandas as pd

solutions_links = get_repos()
solutions = pd.DataFrame(solutions_links, columns=['url'])
solutions['name'] = solutions['url'].apply(get_name)
solutions['content'] = solutions['url'].apply(scrape_solution)

Scraping page /orgs/databricks-industry-solutions/repositories?page=5&type=Repositories
Scraping page /orgs/databricks-industry-solutions/repositories?page=4&type=Repositories
Scraping page /orgs/databricks-industry-solutions/repositories?page=1&type=Repositories
Scraping page /orgs/databricks-industry-solutions/repositories?page=2&type=Repositories
Scraping page /orgs/databricks-industry-solutions/repositories?page=3&type=Repositories
Found 128 solution accelerator(s)


In [0]:
display(solutions)

url name content https://github.com/databricks-industry-solutions/legend-getting-started legend-getting-started In addition to the JDBC connectivity enabled to Databricks from the legend-engine itself, this project helps organizations define data models that can be converted into efficient data pipelines, ensuring data being queried is of high quality and availability. Raw data can be ingested as stream or batch and processed in line with the business semantics defined from the Legend interface. Domain specific language defined in Legend Studio can be interpreted as a series of Spark SQL operations, helping analysts create Delta Lake tables that not only guarantees schema definition but also complies with expectations, derivations and constraints defined by business analysts.

Please check docker folder for basic installation (tested on AWS EC2), notebook for getting started example and pure model for a sample project.

© 2022 Databricks, Inc. All rights reserved. The source in this notebook is provided subject to the Databricks License [https://databricks.com/db-license-source]. All included or referenced third party libraries are subject to the licenses set forth below. https://github.com/databricks-industry-solutions/hls-interop-workshop-jan23 hls-interop-workshop-jan23 To run, import this repo into your Databricks "repo" environment. Make sure you attach necessary cluster resources listed below for your use case.

Please feel free to submit an "issue" in this repo for help https://github.com/databricks-industry-solutions/jsl-kg-cohorts jsl-kg-cohorts Cohort building is an essential part of patient analytics. Defining which patients belong to a cohort, testing the sensitivity of various inclusion and exclusion criteria on sample size, building a control cohort with propensity score matching techniques: These are just some of the processes that healthcare and life sciences researchers live day in and day out, and that's unlikely to change anytime soon. What is changing is the underlying data, the complexity of clinical criteria, and the dynamism demanded by the industry. While tools exist for building patient cohorts based on structured data from EHR data or claims, their practical utility is limited. More and more, cohort building in healthcare and life sciences requires criteria extracted from unstructured and semi-structured clinical documentation with Natural Language Processing (NLP) pipelines. Making this a reality requires a seamless combination of three technologies: (1) a platform that scales for computationally-intensive calculations of massive real world datasets, (2) an accurate NLP library & healthcare-specific models to extract and relate entities from medical documents, and (3) a knowledge graph toolset, able to represent the relationships between a network of entities. In this solution accelerator from John Snow Labs and Databricks, we bring all of this together in the Lakehouse. Read the blog here

SparkNLP for healthcare To create a cluster with access to SparkNLP for healthcare models, follow these steps or run the notebook in this repository to create a cluster with the models. Neo4j To build the knowledge graph, we use neo4j graph database. To learn more on how to stand up a graph database within your cloud environment, see the relevant depplyment guide:

To connect to your graph database from databricks, see Neo4j on databricks

Copyright / License info of the notebook. Copyright [2021] the Notebook Authors. The source in this notebook is provided subject to the Apache 2.0 License. All included or referenced third party libraries are subject to the licenses set forth below.

Databricks Inc. ("Databricks") does not dispense medical, diagnosis, or treatment advice. This Solution Accelerator ("tool") is for informational purposes only and may not be used as a substitute for professional medical advice, treatment, or diagnosis. This tool may not be used within Databricks to process Protected Health Informat

## 1.2 Create vectors
We will split all our content into chunks and compute vector embeddings

In [0]:
from langchain.text_splitter import RecursiveCharacterTextSplitter

def chunk_doc(doc):
  text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=200, separators=[" ", ",", "\n"])
  return text_splitter.split_text(doc)

In [0]:
embeddings = solutions.copy(deep=True)
embeddings['content'] = embeddings['content'].apply(chunk_doc)
embeddings = embeddings.explode('content').reset_index()
embeddings = embeddings.rename({'index': 'id'}, axis=1)

For embeddings, we make use of our public foundational (llama v2) + embedding (BGE) model serving on databricks endpoints.

In [0]:
import mlflow.deployments

def get_embeddings_batch(batch):
  deploy_client = mlflow.deployments.get_deploy_client("databricks")
  response = deploy_client.predict(endpoint="databricks-bge-large-en", inputs={"input": batch})
  return [e['embedding'] for e in response.data]

def get_embeddings(contents):
  max_batch_size = 150
  batches = [contents.iloc[i:i + max_batch_size] for i in range(0, len(contents), max_batch_size)]
  all_embeddings = []
  for batch in batches:
    all_embeddings += get_embeddings_batch(batch.tolist())
  return all_embeddings

In [0]:
vectors = get_embeddings(embeddings['content'])
embeddings['embedding'] = vectors
display(embeddings)

id url name content embedding 0 https://github.com/databricks-industry-solutions/legend-getting-started legend-getting-started In addition to the JDBC connectivity enabled to Databricks from the legend-engine itself, this project helps organizations define data models that can be converted into efficient data pipelines, ensuring data being queried is of high quality and availability. Raw data can be ingested as stream or batch and processed in line with the business semantics defined from the Legend interface. Domain specific language defined in Legend Studio can be interpreted as a series of Spark SQL operations, helping analysts create Delta Lake tables that not only guarantees schema definition but also complies with expectations, derivations and constraints defined by business analysts.

Please check docker folder for basic installation (tested on AWS EC2), notebook for getting started example and pure model for a sample project.

© 2022 Databricks, Inc. All rights reserved. The source in this notebook is provided subject to the Databricks License [https://databricks.com/db-license-source]. All included or List(0.0062103271484375, 0.0092315673828125, -0.035675048828125, -0.01401519775390625, -0.0032062530517578125, -0.003978729248046875, 0.01445770263671875, 0.01267242431640625, 0.0067138671875, 0.054718017578125, -0.011810302734375, -0.0157470703125, 0.053192138671875, -0.0202484130859375, -5.216598510742188E-4, 0.050933837890625, -0.040496826171875, -0.0177764892578125, -0.082275390625, 0.0086212158203125, 0.04217529296875, 0.0221405029296875, -0.0804443359375, -0.048492431640625, -0.044677734375, 0.05133056640625, -0.01403045654296875, 0.01256561279296875, 0.102294921875, 0.02435302734375, -0.05987548828125, -0.00977325439453125, 0.01068878173828125, -0.032257080078125, 0.01415252685546875, 0.017730712890625, -0.008697509765625, 0.006580352783203125, -0.0249176025390625, -0.014251708984375, 0.0106048583984375, -0.0169219970703125, 0.023284912109375, -0.032196044921875, -0.06304931640625, -0.0099639892578125, 0.00926971435546875, -0.052490234375, -0.02178955078125, -0.033905029296875, -0.04034423828125, 8.12530517578125E-4, 0.041107177734375, 0.00862884521484375, 0.001461029052734375, -0.015045166015625, -0.018951416015625, 0.021026611328125, -0.057220458984375, 0.0121917724609375, -0.02044677734375, -0.0155029296875, 0.01861572265625, -0.06695556640625, 0.00933837890625, 0.015411376953125, -0.01629638671875, -0.027557373046875, -0.00641632080078125, -0.0020771026611328125, -0.05853271484375, 0.061492919921875, -0.0301513671875, -0.041717529296875, -0.06103515625, -0.00628662109375, 0.02239990234375, -0.005809783935546875, -0.00536346435546875, 0.006221771240234375, 0.0280303955078125, 0.0280914306640625, 0.02471923828125, -0.00604248046875, -0.045379638671875, -0.0080718994140625, 0.046478271484375, 0.005619049072265625, -1.4257431030273438E-4, -0.0179595947265625, -0.029083251953125, 0.046295166015625, 0.03997802734375, 0.0159149169921875, 0.01543426513671875, 0.0263671875, -0.01806640625, 0.042510986328125, -0.0022258758544921875, 0.0282135009765625, 0.016754150390625, 0.053497314453125, -0.00841522216796875, 0.0047149658203125, -0.008453369140625, -0.00579071044921875, 0.0189361572265625, -0.0010824203491210938, 0.01155853271484375, -0.028411865234375, 0.0302581787109375, -0.060089111328125, 0.024688720703125, -0.0171051025390625, -0.0015497207641601562, 0.004852294921875, 0.0211639404296875, 0.0096282958984375, -0.0202789306640625, -0.041473388671875, -0.001766204833984375, 0.004909515380859375, 0.0274658203125, -0.052764892578125, -0.0147552490234375, -0.040802001953125, 5.860328674316406E-4, 0.024444580078125, -0.04510498046875, -0.031402587890625, 0.0189056396484375, -0.0109100341796875, -0.033172607421875, 0.056610107421875, 0.0218353271484375, 0.00909423828125, 0.054901123046875, 0.0428466796875, 0.0185089111328125, -0.00795745849609375, 0.0241241455078125, -0.023101806640625, -0.0277252197265625, 0.08508300781

We store our new vectors as a delta table that will be synchronized with our vector store thanks to our change data feed enabled.

In [0]:
from pyspark.sql import functions as F

spark.createDataFrame(embeddings) \
  .write \
  .format('delta') \
  .mode('overwrite') \
  .saveAsTable(uc_table_fqn)

In [0]:
_ = sql(f'''ALTER TABLE {uc_table_fqn} SET TBLPROPERTIES (delta.enableChangeDataFeed = true)''')

## 1.3 Index vectors
We create the relevant vector endpoint and index, synchronizing our table and our vector store

In [0]:
import time

def wait_for_vs_endpoint_to_be_ready(vsc, vs_endpoint_name):
  for i in range(180):
    endpoint = vsc.get_endpoint(vs_endpoint_name)
    status = endpoint.get("endpoint_status", endpoint.get("status"))["state"].upper()
    if "ONLINE" in status:
      return endpoint
    elif "PROVISIONING" in status or i < 6:
      if i % 20 == 0: 
        print(f"Waiting for endpoint to be ready, this can take a few min... {endpoint}")
      time.sleep(10)
    else:
      raise Exception(f'Error with the endpoint {vs_endpoint_name}')
  raise Exception(f"Timeout, your endpoint isn't ready yet: {vsc.get_endpoint(vs_endpoint_name)}")

In [0]:
from databricks.vector_search.client import VectorSearchClient
vsc = VectorSearchClient(disable_notice=True)

if vs_endpoint_name not in [e['name'] for e in vsc.list_endpoints()['endpoints']]:
  vsc.create_endpoint(name=vs_endpoint_name, endpoint_type="STANDARD")
  wait_for_vs_endpoint_to_be_ready(vsc, vs_endpoint_name)

In [0]:
def index_exists(vsc, endpoint_name, index_full_name):
  indexes = vsc.list_indexes(endpoint_name).get("vector_indexes", list())
  return any(index_full_name == index.get("name") for index in indexes)

In [0]:
def wait_for_index_to_be_ready(vsc, vs_endpoint_name, index_name):
  for i in range(180):
    idx = vsc.get_index(vs_endpoint_name, index_name).describe()
    index_status = idx.get('status', idx.get('index_status', {}))
    status = index_status.get('detailed_state', index_status.get('status', 'UNKNOWN')).upper()
    url = index_status.get('index_url', index_status.get('url', 'UNKNOWN'))
    if "ONLINE" in status:
      return
    if "UNKNOWN" in status:
      print(f"Can't get the status - will assume index is ready {idx}")
      return
    elif "PROVISIONING" in status:
      if i % 20 == 0: print(f"Waiting for index to be ready, this can take a few min...")
      time.sleep(10)
    else:
        raise Exception(f'''Error with the index - this shouldn't happen. DLT pipeline might have been killed.''')
  raise Exception(f"Timeout, your index isn't ready yet: {vsc.get_index(index_name, vs_endpoint_name)}")

In [0]:
from databricks.sdk import WorkspaceClient
import databricks.sdk.service.catalog as c

if not index_exists(vsc, vs_endpoint_name, vs_index_fqn):
  print(f"Creating index {vs_index_fqn} on endpoint {vs_endpoint_name}...")

  vsc.create_delta_sync_index(
    endpoint_name=vs_endpoint_name,
    index_name=vs_index_fqn,
    source_table_name=uc_table_fqn,
    pipeline_type="CONTINUOUS",
    primary_key="id",
    embedding_dimension=1024, # Match your model embedding size (bge)
    embedding_vector_column="embedding"
  )

  wait_for_index_to_be_ready(vsc, vs_endpoint_name, vs_index_fqn)

Creating index antoine_amend.sgtm_genai.solution_accelerators_vectors on endpoint shared-demo-endpoint...
Waiting for index to be ready, this can take a few min... {'detailed_state': 'PROVISIONING_PIPELINE_RESOURCES', 'message': 'Index is currently pending setup of pipeline resources. Check latest status in Delta Live Tables: https://e2-demo-field-eng.cloud.databricks.com#joblist/pipelines/ac340456-9fca-45aa-93e8-c55492f0f9f2/updates/48f2f5be-bd43-422d-a5fb-22121ee5dc73', 'indexed_row_count': 0, 'provisioning_status': {}, 'ready': False, 'index_url': 'e2-demo-field-eng.cloud.databricks.com/api/2.0/vector-search/endpoints/shared-demo-endpoint/indexes/antoine_amend.sgtm_genai.solution_accelerators_vectors'} - pipeline url:e2-demo-field-eng.cloud.databricks.com/api/2.0/vector-search/endpoints/shared-demo-endpoint/indexes/antoine_amend.sgtm_genai.solution_accelerators_vectors
Waiting for index to be ready, this can take a few min... {'detailed_state': 'PROVISIONING_PIPELINE_RESOURCES', 'me

## 1.4 Test vector store

In [0]:
query = "Does Databricks offer any solution accelerator that can extract text from unstructured data?"
question = {"query": query}

In [0]:
import mlflow.deployments
from databricks.vector_search.client import VectorSearchClient

deploy_client = mlflow.deployments.get_deploy_client("databricks")
response = deploy_client.predict(endpoint="databricks-bge-large-en", inputs={"input": [query]})
embeddings = [e['embedding'] for e in response.data]

vsc = VectorSearchClient(disable_notice=True)
results = vsc.get_index(vs_endpoint_name, vs_index_fqn).similarity_search(
  query_vector=embeddings[0],
  columns=["url", "name", "content"],
  num_results=1)
docs = results.get('result', {}).get('data_array', [])
docs

[['https://github.com/databricks-industry-solutions/digitization-documents',
  'digitization-documents',
  'recognition (OCR) and natural language processing (NLP) in order to transform any financial document, in any format, into valuable data assets. The Apache Tika toolkit detects and extracts metadata and text from over a thousand different file types (such as PPT, XLS, and PDF). Combined with Tesseract, the most commonly used OCR technology, there is literally no limit to what files we can ingest, store and exploit for analytics / operation purpose. In this solution, we will use our newly released spark input format tika-ocr to extract text from PDF reports available online\n\n© 2022 Databricks, Inc. All rights reserved. The source in this notebook is provided subject to the Databricks License [https://databricks.com/db-license-source]. All included or referenced third party libraries are subject to the licenses set forth below.',
  0.65567917]]

# 2. Create chatbot
With our vector store in place, we can build our simple chat bot that we intend to serve on MLFlow serving

## 1. Vector retriever

In [0]:
import os
db_token = dbutils.secrets.get(scope=db_secret_scope, key=db_secret_key)
db_host = 'https://{}'.format(spark.conf.get("spark.databricks.workspaceUrl"))

# This variable will be used in the context of this notebook
# Note that the same needs to be set in our serving endpoint 
os.environ['DATABRICKS_TOKEN'] = db_token
os.environ['DATABRICKS_HOST'] = db_host

In [0]:
from databricks.vector_search.client import VectorSearchClient
from langchain.vectorstores import DatabricksVectorSearch
from langchain.embeddings import DatabricksEmbeddings

def get_vector_store(persist_dir: str = None):
    vsc = VectorSearchClient(workspace_url=os.environ["DATABRICKS_HOST"], personal_access_token=os.environ["DATABRICKS_TOKEN"], disable_notice=True)
    vs_index = vsc.get_index(endpoint_name=vs_endpoint_name, index_name=vs_index_fqn)
    embedding_model = DatabricksEmbeddings(endpoint="databricks-bge-large-en")
    return DatabricksVectorSearch(vs_index, text_column="content", embedding=embedding_model, columns=['url', 'name'])

def get_vector_store_as_retriever(persist_dir: str = None):
    vectorstore = get_vector_store(persist_dir)
    return vectorstore.as_retriever(search_kwargs={"score_threshold": .5, "k": 1})

In [0]:
vectorstore = get_vector_store_as_retriever()
similar_documents = vectorstore.get_relevant_documents(query)
print(f"Relevant documents: {similar_documents[0]}")

Relevant documents: page_content='recognition (OCR) and natural language processing (NLP) in order to transform any financial document, in any format, into valuable data assets. The Apache Tika toolkit detects and extracts metadata and text from over a thousand different file types (such as PPT, XLS, and PDF). Combined with Tesseract, the most commonly used OCR technology, there is literally no limit to what files we can ingest, store and exploit for analytics / operation purpose. In this solution, we will use our newly released spark input format tika-ocr to extract text from PDF reports available online\n\n© 2022 Databricks, Inc. All rights reserved. The source in this notebook is provided subject to the Databricks License [https://databricks.com/db-license-source]. All included or referenced third party libraries are subject to the licenses set forth below.' metadata={'url': 'https://github.com/databricks-industry-solutions/digitization-documents', 'name': 'digitization-documents', 

## 2. Build chains
We handle business logic through langchain framework. Note that being served on MLFlow, our model will have no concept of memory. We will add memory later as our product keeps evolving.

In [0]:
from langchain.chat_models import ChatDatabricks

def get_chat_model():
  return ChatDatabricks(endpoint="databricks-llama-2-70b-chat", max_tokens=200)

In [0]:
from langchain.chains import RetrievalQA
from langchain.prompts import PromptTemplate

prompt_template = """You are an assistant for Databricks users. You are answering questions relative to industry challenges solved by the Databricks solution accelerators. If the question is not related to one of these topics, kindly decline to answer. If you don't know the answer, just say that you don't know, don't try to make up an answer. Keep the answer as concise as possible.
Use the following pieces of context to answer the question at the end:
{context}
Question: {question}
Answer:"""

prompt = PromptTemplate(template=prompt_template, input_variables=["context", "question"])

chain = RetrievalQA.from_chain_type(
    llm=get_chat_model(),
    return_source_documents=True,
    chain_type="stuff",
    retriever=get_vector_store_as_retriever(),
    chain_type_kwargs={"prompt": prompt, "verbose": False}
)

In [0]:
answer = chain({"query": query})
print(answer['result'])
print('\n')
print('References:')
for i, supporting_doc in enumerate(answer['source_documents']):
  print('- {}'.format(supporting_doc.metadata['url']))

Yes, Databricks offers a solution accelerator that can extract text from unstructured data using Optical Character Recognition (OCR) and Natural Language Processing (NLP) capabilities. The solution leverages the Apache Tika toolkit and Tesseract OCR technology to detect and extract metadata and text from various file types, including PDF, PPT, and XLS. The extracted text can then be used for analytics and operational purposes. The solution accelerator is available through the spark input format tika-ocr, which is a newly released feature in Databricks.


References:
- https://github.com/databricks-industry-solutions/digitization-documents


## 3. Create model
We can use pyfunc to embed our entire langchain as a self service model governed on unity catalog

In [0]:
import mlflow
from mlflow.pyfunc import PythonModel

class QABot(PythonModel):

  @classmethod
  def __init__(self, db_host, chain):
    self.db_host = db_host
    self.chain = chain

  @classmethod
  def predict_record(self, query):

    # Note that DATABRICKS_TOKEN will be set from the endpoint configuration directly, passed as a secret
    import os
    os.environ['DATABRICKS_HOST'] = db_host

    # Run actual model
    chain_output = self.chain({"query": query})

    # Handle output to return both answer and reference link
    answer = chain_output['result']
    references = chain_output['source_documents']
    references = [reference.metadata['url'] for reference in references]
    
    # JSON serialization will be handled via pandas dataframe
    return [answer, references]

  @classmethod
  def predict(self, context, model_input):
    import pandas as pd
    import numpy as np
    if isinstance(model_input, pd.DataFrame):
      query = model_input.iloc[0]['query']
    else:
      raise Exception('Model input does not match model signature')
    return pd.DataFrame([self.predict_record(query)], columns=['answer', 'references'])

In [0]:
python_model = QABot(db_host, chain)

import pandas as pd
model_input = pd.DataFrame([query], columns=['query'])
model_output = python_model.predict(None, model_input)
print(model_output['answer'])

0    Yes, Databricks offers a solution accelerator ...
Name: answer, dtype: object


In [0]:
from mlflow.models import infer_signature
model_signature = infer_signature(model_input, model_output)
model_signature

inputs: 
  ['query': string]
outputs: 
  ['answer': string, 'references': string]
params: 
  None

In [0]:
from mlflow.models import infer_signature
import mlflow

with mlflow.start_run(run_name=uc_model_name) as run:
    mlflow.pyfunc.log_model("model", 
                            python_model=python_model, 
                            signature=model_signature, 
                            pip_requirements=[
                                f"mlflow",
                                "git+https://github.com/langchain-ai/langchain.git@master#subdirectory=libs/langchain", 
                                "git+https://github.com/mlflow/mlflow.git@gateway-migration", 
                                "databricks-vectorsearch==0.21", 
                            ],
                            input_example=model_input
                            )
print(run.info.run_id)

Uploading artifacts:   0%|          | 0/6 [00:00<?, ?it/s]

3e8dcea549d24cb5980fffa3f3515937


In [0]:
from mlflow.tracking import MlflowClient

mlflow.set_registry_uri("databricks-uc")
model_fqname = f"{uc_catalog_name}.{uc_schema_name}.{uc_model_name}"
client = MlflowClient()
latest_model = mlflow.register_model(f'runs:/{run.info.run_id}/model', model_fqname)
client.set_registered_model_alias(model_fqname, "production", latest_model.version)

Registered model 'antoine_amend.sgtm_genai.slack-bot-genai' already exists. Creating a new version of this model...


Uploading artifacts:   0%|          | 0/6 [00:00<?, ?it/s]

Created version '13' of model 'antoine_amend.sgtm_genai.slack-bot-genai'.


Temporary hack, this is not needed when vector search is fully available through langchain. Meanwhile, we need to package our model as a fully contained dependency.
Note that this will result in a new model version

In [0]:
import mlflow.models.utils
mlflow.models.utils.add_libraries_to_model(
    f"models:/{model_fqname}/{latest_model.version}"
)

model_version = int(latest_model.version) + 1

2023/12/07 17:31:30 WARNING mlflow.models.model: Model logged without a signature. Signatures will be required for upcoming model registry features as they validate model inputs and denote the expected schema of model outputs. Please visit https://www.mlflow.org/docs/2.8.2/models.html#set-signature-on-logged-model for instructions on setting a model signature on your logged model.


Uploading artifacts:   0%|          | 0/89 [00:00<?, ?it/s]

2023/12/07 17:32:24 INFO mlflow.store.artifact.cloud_artifact_repo: The progress bar can be disabled by setting the environment variable MLFLOW_ENABLE_ARTIFACTS_PROGRESS_BAR to false
Registered model 'antoine_amend.sgtm_genai.slack-bot-genai' already exists. Creating a new version of this model...


Uploading artifacts:   0%|          | 0/89 [00:00<?, ?it/s]

2023/12/07 17:32:31 INFO mlflow.store.artifact.cloud_artifact_repo: The progress bar can be disabled by setting the environment variable MLFLOW_ENABLE_ARTIFACTS_PROGRESS_BAR to false
Created version '14' of model 'antoine_amend.sgtm_genai.slack-bot-genai'.


# 3. Serving endpoint
And finally serve this model on MLFlow serving. Exposing an HTTP API, we will interact with our model from our slack application

In [0]:
from databricks.sdk import WorkspaceClient
from databricks.sdk.service.serving import EndpointCoreConfigInput, ServedModelInput

w = WorkspaceClient()
endpoint_config = EndpointCoreConfigInput(
    name=uc_model_name,
    served_models=[
        ServedModelInput(
            model_name=model_fqname,
            model_version=model_version,
            workload_size="Small",
            scale_to_zero_enabled=True,
            environment_vars={
                # export environment variable as a secret
                "DATABRICKS_TOKEN": f"{{{{secrets/{db_secret_scope}/{db_secret_key}}}}}"
            }
        )
    ]
)

existing_endpoint = next(
    (e for e in w.serving_endpoints.list() if e.name == uc_model_name), None
)
if existing_endpoint == None:
    print(f"Creating the endpoint {uc_model_name}, this will take a few minutes to package and deploy the endpoint...")
    w.serving_endpoints.create_and_wait(name=uc_model_name, config=endpoint_config)
else:
    print(f"Updating the endpoint {uc_model_name} to version {latest_model_version}, this will take a few minutes to package and deploy the endpoint...")
    w.serving_endpoints.update_config_and_wait(served_models=endpoint_config.served_models, name=uc_model_name)

Creating the endpoint slack-bot-genai, this will take a few minutes to package and deploy the endpoint...
